In [6]:
import numpy as np
import pandas as pd
import re

In [7]:
pd.set_option('display.max_rows',None)
pd.set_option('display.max_columns',None)
pd.set_option('display.max_colwidth',None)

In [8]:
df = pd.read_csv('/content/gurgaon_properties_cleaned_v1.csv')

In [9]:
df.head(1)
# focus on - > areaWithType, additionalRoom, agePossession, furnishDetails, features

property_type        society     sector  price  price_per_sqft    area  \
0          flat  tulip ivory3.  sector 70    2.0          8333.0  2400.0   

                                                                    areaWithType  \
0  Super Built up area 2400(222.97 sq.m.)Carpet area: 1850 sq.ft. (171.87 sq.m.)   

   bedRoom  bathroom balcony additionalRoom  floorNum facing  \
0      4.0       5.0      3+   servant room       6.0   East   

      agePossession  \
0  5 to 10 Year Old   

                                                                                                                                                                                                                                                                            nearbyLocations  \
0  ['Reach 3 Roads Shopping Mall', 'Southern Periphery Road', 'Indus World School', 'DPG Institute of Technology', 'Polaris Hospital', 'Indira Gandhi International Airport', 'IMT Manesar', 'Radisson Hotel Sohna Road', 'SkyJumper Trampoline Park', 'SportsCube Center(Sports Complex)']   

                                                                                                                                                                                                                                                    furnishDetails  \
0  ['4 Wardrobe', '7 Fan', '1 Exhaust Fan', '5 Geyser', '9 Light', '1 Modular Kitchen', 'No AC', 'No Bed', 'No Chimney', 'No Curtains', 'No Dining Table', 'No Microwave', 'No Fridge', 'No Sofa', 'No Stove', 'No TV', 'No Washing Machine', 'No Water Purifier']   

                                                                                                                                                                                                                                                                                                                                                                                                              features  
0  ['Security / Fire Alarm', 'Power Back-up', 'Feng Shui / Vaastu Compliant', 'Intercom Facility', 'Lift(s)', 'High Ceiling Height', 'Maintenance Staff', 'Water Storage', 'Separate entry for servant room', 'Piped-gas', 'Visitor Parking', 'Swimming Pool', 'Park', 'Shopping Centre', 'Fitness Centre / GYM', 'Waste Disposal', 'Rain Water Harvesting', 'Club house / Community Center', 'Water softening plant']

### areaWithType

- spend time with data

- carpet area -> the actual living space
- builtup area -> carpet area + thickness of walls + balcony
- super built up area -> staircase, garden, parking etc.
- plot area is for houses, uper wale sab flat k the

In [10]:
df[['area','areaWithType']].sample(5)

area  \
1997  2350.0   
2519   360.0   
180   1650.0   
2355  3400.0   
3774  2400.0   

                                                                      areaWithType  
1997                                        Super Built up area 2350(218.32 sq.m.)  
2519                                                   Plot area 400(334.45 sq.m.)  
180   Super Built up area 1650(153.29 sq.m.)Carpet area: 1155 sq.ft. (107.3 sq.m.)  
2355                                        Super Built up area 3400(315.87 sq.m.)  
3774                                            Built Up area: 2400 (222.97 sq.m.)

# 1. areaWithType

### problem kya hai ?

- yee jo area wala col hai yee consistent nai hai, kahe p 'area' as in carpet area mention hai. kahe kahe p 'area' as super built up area. kahe p 'area' is reffered as built up area.

### solution
- create 3 new cols from areaWithType cols - `super_built_up_area`,`built_up_area`,`carpet_area`

In [11]:
# this func extracts the super built up area
def get_super_built_up_area(text):
  match = re.search(r'Super Built up area (\d+\.?\d*)',text)
  if match:
    return float(match.group(1))
  return None

In [21]:
# this function extracts the built up area or carpet area
def get_area(text, area_type):
  if not isinstance(text, str):
    return None
  match = re.search(area_type + r'\s*:\s*(\d+\.?\d*)',text)
  if match:
    return float(match.group(1))
  return None

In [13]:
# # this function checks if the area is provided in sq.m and converts it to sqft if needed
# def convert_to_sqft(text, area_value):
#   if area_value is None:
#     return None
#   match = re.search(r'{} \((\d+\.?\d*) sq.m. \)'. format(area_value), text)
#   if match:
#     sq_m_value = float(match.group(1))
#     return sq_m_value * 10.7639 # conversion factor from sq.m to sqft
#   return area_value

In [17]:
import re

def convert_to_sqft(text, area_value):
    if area_value is None or not isinstance(text, str):
        return area_value

    try:
        pattern = r'{} \((\d+\.?\d*) sq\.m\. \)'.format(re.escape(str(area_value)))
        match = re.search(pattern, text)
        if match:
            sq_m_value = float(match.group(1))
            return round(sq_m_value * 10.7639, 2)  # optional: round to 2 decimals
    except Exception as e:
        print(f"Error in convert_to_sqft with input ({text}, {area_value}): {e}")

    return area_value

In [15]:
df['super_built_up_area'].astype('str')

0        2400.0
1        1976.0
2        2000.0
3        2047.0
4        1660.0
5        1500.0
6           nan
7        1269.0
8        1210.0
9        3400.0
10       1103.0
11          nan
12          nan
13          nan
14        380.0
15       1776.0
16       1435.0
17          nan
18          nan
19          nan
20          nan
21          nan
22       1776.0
23       1877.0
24       1336.0
25          nan
26       2585.0
27       2390.0
28          nan
29          nan
30          nan
31          nan
32        623.0
33       2950.0
34       3557.0
35       3150.0
36          nan
37       3400.0
38       1406.0
39          nan
40       1550.0
41       2000.0
42          nan
43       2997.0
44          nan
45          nan
46          nan
47       2000.0
48          nan
49          nan
50          nan
51          nan
52          nan
53       1380.0
54       1395.0
55        406.0
56       1790.0
57       1741.0
58       1579.0
59       1590.0
60       4500.0
61          nan
62          nan
63       1245.0
64          nan
65          nan
66          nan
67       1381.0
68        624.0
69          nan
70       1415.0
71       1818.0
72          nan
73       2010.0
74       1245.0
75          nan
76       4200.0
77          nan
78       2250.0
79       4200.0
80          nan
81          nan
82          nan
83       1508.0
84          nan
85       2025.0
86          nan
87          nan
88          nan
89       3482.0
90       3931.0
91        500.0
92       1735.0
93       1980.0
94          nan
95          nan
96          nan
97       4848.0
98       2003.0
99          nan
100         nan
101         nan
102         nan
103      1950.0
104         nan
105      2605.0
106      1790.0
107      2727.0
108         nan
109         nan
110         nan
111      2660.0
112         nan
113      1789.0
114         nan
115         nan
116         nan
117      1650.0
118         nan
119       700.0
120       650.0
121      2150.0
122         nan
123      1457.0
124      2149.0
125      1304.0
126         nan
127      1565.0
128      1929.0
129         nan
130      1741.0
131      2305.0
132      1534.0
133      2754.0
134      1692.0
135      1650.0
136      1920.0
137         nan
138         nan
139      1640.0
140      1900.0
141         nan
142         nan
143         nan
144         nan
145      1140.0
146      1805.0
147       548.0
148         nan
149         nan
150      2690.0
151      3130.0
152         nan
153         nan
154         nan
155      1350.0
156      2430.0
157      1559.0
158      1275.0
159      3400.0
160      1470.0
161         nan
162         nan
163         nan
164      1398.0
165         nan
166         nan
167     1748.87
168         nan
169      1276.0
170      2875.0
171      2400.0
172         nan
173         nan
174         nan
175         nan
176         nan
177         nan
178         nan
179      2361.0
180      1650.0
181         nan
182         nan
183         nan
184         nan
185         nan
186         nan
187      1366.0
188      1516.0
189      2095.0
190      2125.0
191         nan
192       583.0
193      2400.0
194      1950.0
195         nan
196         nan
197      2660.0
198         nan
199       735.0
200         nan
201      1799.0
202      1755.0
203         nan
204      1550.0
205         nan
206         nan
207         nan
208         nan
209      1818.0
210      1360.0
211         nan
212      1805.0
213      1565.0
214      3198.0
215         nan
216      1743.0
217         nan
218      2025.0
219      1245.0
220      1457.0
221         nan
222      1805.0
223         nan
224         nan
225      1990.0
226      1300.0
227      1350.0
228      1360.0
229         nan
230         nan
231         nan
232         nan
233      3363.0
234         nan
235      1755.0
236      1081.0
237      2812.0
238      1755.0
239         nan
240      3150.0
241      2290.0
242         nan
243      1930.0
244      2000.0
245         nan
246     2251.42
247      1852.0
248      2103.0
249         nan


In [22]:
# Extract super built up area and convert to sqft if needed
df['super_built_up_area'] = df['areaWithType'].astype('str').apply(get_super_built_up_area)
df['super_built_up_area'] = df.apply(lambda x:convert_to_sqft(x['areaWithType'],x['super_built_up_area']),axis=1)

# Extracting built up area and converting to sqft
df['built_up_area'] = df['areaWithType'].apply(lambda x:get_area(x,'Built Up area'))
df['build_up_area'] = df.apply(lambda x: convert_to_sqft(x['areaWithType'], x['built_up_area']),axis = 1)

# Extracting Carpet Area and Convert to sqft
df['carpet_area'] = df['areaWithType'].apply(lambda x: get_area(x,'Carpet area'))
df['carpet_area'] = df.apply(lambda x: convert_to_sqft(x['areaWithType'], x['carpet_area']),axis=1)

In [32]:
df[['price','property_type','area','areaWithType','super_built_up_area','built_up_area','carpet_area']].sample(5)

price property_type    area  \
1310   0.55         house     6.0   
1607   1.18          flat  1383.0   
17     1.07          flat  1299.0   
3801   0.78          flat  1010.0   
863    1.05          flat   997.0   

                                                                    areaWithType  \
1310                                               Built Up area: 56 (5.2 sq.m.)   
1607                                      Super Built up area 1383(128.48 sq.m.)   
17                                              Carpet area: 1305 (121.24 sq.m.)   
3801  Super Built up area 1010(93.83 sq.m.)Carpet area: 700 sq.ft. (65.03 sq.m.)   
863                                               Carpet area: 997 (92.62 sq.m.)   

      super_built_up_area  built_up_area  carpet_area  
1310                  NaN           56.0          NaN  
1607               1383.0            NaN          NaN  
17                    NaN            NaN       1305.0  
3801               1010.0            NaN        700.0  
863                   NaN            NaN        997.0

In [33]:
df.duplicated().sum()

np.int64(122)

In [34]:
df[~((df['super_built_up_area'].isnull()) | (df['built_up_area'].isnull()) | (df['carpet_area'].isnull()))][['price','property_type','area','areaWithType','super_built_up_area','built_up_area','carpet_area']].shape

(534, 7)

In [37]:
df[df['areaWithType'].str.contains('Plot',na = False)][['price','property_type','area','areaWithType','super_built_up_area','built_up_area','carpet_area']].head(5)

price property_type   area  \
6    9.50         house  237.0   
12   2.68         house  156.0   
28   6.20         house  243.0   
29  19.00         house  600.0   
30   3.40         house  225.0   

                                                           areaWithType  \
6                                            Plot area 263(219.9 sq.m.)   
12                                          Plot area 173(144.65 sq.m.)   
28                                          Plot area 270(225.75 sq.m.)   
29  Plot area 9000(836.13 sq.m.)Carpet area: 6000 sq.ft. (557.42 sq.m.)   
30                                          Plot area 250(209.03 sq.m.)   

    super_built_up_area  built_up_area  carpet_area  
6                   NaN            NaN          NaN  
12                  NaN            NaN          NaN  
28                  NaN            NaN          NaN  
29                  NaN            NaN       6000.0  
30                  NaN            NaN          NaN

In [38]:
df.isnull().sum()

property_type             1
society                   2
sector                    0
price                    30
price_per_sqft           30
area                     30
areaWithType              1
bedRoom                   1
bathroom                  1
balcony                   1
additionalRoom            1
floorNum                 20
facing                 1113
agePossession             2
nearbyLocations         182
furnishDetails          990
features                643
super_built_up_area    1899
built_up_area          2626
build_up_area          2626
carpet_area            1866
dtype: int64

In [88]:
all_nan_df = df[((df['super_built_up_area'].isnull()) & (df['built_up_area'].isnull()) & (df['carpet_area'].isnull()))][['price','property_type','area','areaWithType','super_built_up_area','built_up_area','carpet_area']]

In [89]:
all_nan_df.head()

price property_type   area                 areaWithType  \
6    9.50         house  237.0   Plot area 263(219.9 sq.m.)   
12   2.68         house  156.0  Plot area 173(144.65 sq.m.)   
28   6.20         house  243.0  Plot area 270(225.75 sq.m.)   
30   3.40         house  225.0  Plot area 250(209.03 sq.m.)   
39   2.75         house  156.0  Plot area 173(144.65 sq.m.)   

    super_built_up_area  built_up_area  carpet_area  
6                   NaN            NaN          NaN  
12                  NaN            NaN          NaN  
28                  NaN            NaN          NaN  
30                  NaN            NaN          NaN  
39                  NaN            NaN          NaN

In [90]:
all_nan_index = df[((df['super_built_up_area'].isnull()) & (df['built_up_area'].isnull()) & (df['carpet_area'].isnull()))][['price','property_type','area','areaWithType','super_built_up_area','built_up_area','carpet_area']].index

In [91]:
# Function to extract plot area from 'areaWithType' column
def extract_plot_area(area_with_type):
    if pd.isna(area_with_type):
      return None
    match = re.search(r'Plot area (\d+\.?\d*)', area_with_type)
    return float(match.group(1)) if match else None

In [92]:
all_nan_df['built_up_area'] = all_nan_df['areaWithType'].apply(extract_plot_area)

In [94]:
all_nan_df.head()

price property_type   area                 areaWithType  \
6    9.50         house  237.0   Plot area 263(219.9 sq.m.)   
12   2.68         house  156.0  Plot area 173(144.65 sq.m.)   
28   6.20         house  243.0  Plot area 270(225.75 sq.m.)   
30   3.40         house  225.0  Plot area 250(209.03 sq.m.)   
39   2.75         house  156.0  Plot area 173(144.65 sq.m.)   

    super_built_up_area  built_up_area  carpet_area  
6                   NaN          263.0          NaN  
12                  NaN          173.0          NaN  
28                  NaN          270.0          NaN  
30                  NaN          250.0          NaN  
39                  NaN          173.0          NaN

In [95]:
temp_df = all_nan_df

In [96]:
temp_df.head()

price property_type   area                 areaWithType  \
6    9.50         house  237.0   Plot area 263(219.9 sq.m.)   
12   2.68         house  156.0  Plot area 173(144.65 sq.m.)   
28   6.20         house  243.0  Plot area 270(225.75 sq.m.)   
30   3.40         house  225.0  Plot area 250(209.03 sq.m.)   
39   2.75         house  156.0  Plot area 173(144.65 sq.m.)   

    super_built_up_area  built_up_area  carpet_area  
6                   NaN          263.0          NaN  
12                  NaN          173.0          NaN  
28                  NaN          270.0          NaN  
30                  NaN          250.0          NaN  
39                  NaN          173.0          NaN

In [97]:
temp_df['area'] = temp_df['area']*10

In [100]:
temp_df[temp_df['price'] == 5.50]

price property_type    area                  areaWithType  \
554     5.5         house  1800.0   Plot area 200(167.23 sq.m.)   
560     5.5         house  2590.0    Plot area 288(240.8 sq.m.)   
563     5.5         house  1800.0   Plot area 200(167.23 sq.m.)   
970     5.5         house  2380.0   Plot area 265(221.57 sq.m.)   
1305    5.5         house  4200.0  Plot area 4200(390.19 sq.m.)   
1370    5.5         house  2340.0   Plot area 260(217.39 sq.m.)   
1454    5.5         house  1000.0    Plot area 1000(92.9 sq.m.)   
1802    5.5         house  1440.0   Plot area 160(133.78 sq.m.)   
2015    5.5         house   300.0    Plot area 300(27.87 sq.m.)   
2176    5.5         house  2520.0   Plot area 280(234.12 sq.m.)   
2269    5.5         house  2550.0   Plot area 270(225.75 sq.m.)   
2489    5.5         house  1800.0   Plot area 200(167.23 sq.m.)   
3015    5.5         house  1930.0   Plot area 215(179.77 sq.m.)   

      super_built_up_area  built_up_area  carpet_area  
554                   NaN          200.0          NaN  
560                   NaN          288.0          NaN  
563                   NaN          200.0          NaN  
970                   NaN          265.0          NaN  
1305                  NaN         4200.0          NaN  
1370                  NaN          260.0          NaN  
1454                  NaN         1000.0          NaN  
1802                  NaN          160.0          NaN  
2015                  NaN          300.0          NaN  
2176                  NaN          280.0          NaN  
2269                  NaN          270.0          NaN  
2489                  NaN          200.0          NaN  
3015                  NaN          215.0          NaN

In [101]:
all_nan_df = temp_df

In [102]:
def convert_scale(row):
    if np.isnan(row['area']) or np.isnan(row['built_up_area']):
        return row['built_up_area']
    else:
        if round(row['area']/row['built_up_area']) == 9.0:
            return row['built_up_area'] * 9
        elif round(row['area']/row['built_up_area']) == 11.0:
            return row['built_up_area'] * 10.7
        else:
            return row['built_up_area']

In [103]:
all_nan_df['built_up_area'] = all_nan_df.apply(convert_scale,axis=1)

In [104]:
all_nan_df

price property_type      area                     areaWithType  \
6      9.50         house    2370.0       Plot area 263(219.9 sq.m.)   
12     2.68         house    1560.0      Plot area 173(144.65 sq.m.)   
28     6.20         house    2430.0      Plot area 270(225.75 sq.m.)   
30     3.40         house    2250.0      Plot area 250(209.03 sq.m.)   
39     2.75         house    1560.0      Plot area 173(144.65 sq.m.)   
42     7.00         house    2470.0      Plot area 275(229.94 sq.m.)   
48     0.95         house    1070.0      Plot area 1065(98.94 sq.m.)   
50     1.35         house    3500.0     Plot area 3500(325.16 sq.m.)   
52     6.95         house    1800.0      Plot area 192(160.54 sq.m.)   
62     5.00         house    2250.0      Plot area 250(209.03 sq.m.)   
65     8.50         house    3240.0      Plot area 360(301.01 sq.m.)   
72     9.54         house    3240.0      Plot area 360(301.01 sq.m.)   
88    10.85         house    3760.0       Plot area 418(349.5 sq.m.)   
100    3.25         house    1070.0   Plot area 1069.63(99.37 sq.m.)   
104    5.15         house    1930.0      Plot area 215(179.77 sq.m.)   
114    5.00         house    2370.0       Plot area 263(219.9 sq.m.)   
115    5.00         house    2370.0       Plot area 263(219.9 sq.m.)   
143    0.50         house     450.0       Plot area 450(41.81 sq.m.)   
149    8.50         house    4000.0     Plot area 4000(371.61 sq.m.)   
154   11.50         house    4680.0      Plot area 520(434.79 sq.m.)   
174   13.00         house    2700.0      Plot area 300(250.84 sq.m.)   
182    1.07         house     900.0       Plot area 900(83.61 sq.m.)   
184    0.89         house     480.0       Plot area 477(44.31 sq.m.)   
186    4.50         house    4950.0      Plot area 550(459.87 sq.m.)   
195    9.00         house    3240.0      Plot area 360(301.01 sq.m.)   
196   11.00         house    3240.0      Plot area 360(301.01 sq.m.)   
200    3.10         house    2250.0      Plot area 250(209.03 sq.m.)   
207    2.40         house     900.0       Plot area 100(83.61 sq.m.)   
229    9.55         house    4950.0      Plot area 550(459.87 sq.m.)   
230    7.25         house    2590.0       Plot area 288(240.8 sq.m.)   
260    0.40         house     450.0        Plot area 50(41.81 sq.m.)   
264    2.25         house    1440.0      Plot area 160(133.78 sq.m.)   
271    4.99         house    2640.0      Plot area 270(225.75 sq.m.)   
276    3.30         house    1730.0      Plot area 192(160.54 sq.m.)   
278    4.70         house    2160.0      Plot area 240(200.67 sq.m.)   
288    1.44         house     540.0        Plot area 60(50.17 sq.m.)   
296    0.70         house     680.0       Plot area 684(63.55 sq.m.)   
301    5.40         house    2610.0      Plot area 290(242.48 sq.m.)   
307     NaN         house       NaN      Plot area 670(560.21 sq.m.)   
311   10.50         house     400.0       Plot area 402(37.35 sq.m.)   
313    2.10         house     550.0           Plot area 61(51 sq.m.)   
320    2.95         house    1850.0      Plot area 205(171.41 sq.m.)   
337    5.70         house    2520.0      Plot area 270(225.75 sq.m.)   
340    0.45         house     900.0       Plot area 900(83.61 sq.m.)   
342    3.00         house    1560.0      Plot area 173(144.65 sq.m.)   
365    4.45         house    2880.0      Plot area 320(267.56 sq.m.)   
368    8.50         house    3240.0      Plot area 360(301.01 sq.m.)   
370    8.45         house     360.0       Plot area 359(33.35 sq.m.)   
372    4.35         house    5480.0     Plot area 5480(509.11 sq.m.)   
378   10.85         house    2840.0      Plot area 316(264.22 sq.m.)   
379    3.50         house    1450.0      Plot area 161(134.62 sq.m.)   
387   15.50         house    5490.0      Plot area 610(510.04 sq.m.)   
392    6.50         house    1800.0      Plot area 200(167.23 sq.m.)   
410    6.75         house    6230.0       Plot area 692(578.6 sq.m.)   
434    3.50         house    2610.0      Plot 

In [105]:
all_nan_df[all_nan_df['price'] == 15.50]

price property_type    area                 areaWithType  \
387    15.5         house  5490.0  Plot area 610(510.04 sq.m.)   
2880   15.5         house  4520.0  Plot area 502(419.74 sq.m.)   

      super_built_up_area  built_up_area  carpet_area  
387                   NaN         5490.0          NaN  
2880                  NaN         4518.0          NaN

In [106]:
df.update(all_nan_df)

In [107]:
df.isnull().sum()

property_type             1
society                   2
sector                    0
price                    30
price_per_sqft           30
area                     30
areaWithType              1
bedRoom                   1
bathroom                  1
balcony                   1
additionalRoom            1
floorNum                 20
facing                 1113
agePossession             2
nearbyLocations         182
furnishDetails          990
features                643
super_built_up_area    1899
built_up_area          2080
build_up_area          2626
carpet_area            1866
dtype: int64

In [108]:
df.head()

property_type                     society      sector  price  \
0          flat               tulip ivory3.   sector 70   2.00   
1          flat      capital residences 360  sector 70a   1.69   
2          flat          emaar palm premier   sector 77   2.10   
3          flat                m3m merlin3.   sector 67   2.65   
4          flat  dnha group housing society     manesar   0.75   

   price_per_sqft    area  \
0          8333.0  2400.0   
1          8552.0  1976.0   
2         10500.0  2000.0   
3         12945.0  2047.0   
4          4518.0  1660.0   

                                                                                                             areaWithType  \
0                                           Super Built up area 2400(222.97 sq.m.)Carpet area: 1850 sq.ft. (171.87 sq.m.)   
1  Super Built up area 1976(183.58 sq.m.)Built Up area: 1900 sq.ft. (176.52 sq.m.)Carpet area: 1650 sq.ft. (153.29 sq.m.)   
2  Super Built up area 2000(185.81 sq.m.)Built Up area: 1600 sq.ft. (148.64 sq.m.)Carpet area: 1500 sq.ft. (139.35 sq.m.)   
3  Super Built up area 2047(190.17 sq.m.)Built Up area: 1900 sq.ft. (176.52 sq.m.)Carpet area: 1700 sq.ft. (157.94 sq.m.)   
4                                                                                  Super Built up area 1660(154.22 sq.m.)   

   bedRoom  bathroom balcony additionalRoom  floorNum      facing  \
0      4.0       5.0      3+   servant room       6.0        East   
1      3.0       3.0      3+   servant room       8.0  North-East   
2      3.0       4.0      3+   servant room      11.0         NaN   
3      3.0       3.0       3         others       0.0  North-East   
4      3.0       2.0       2  not available       5.0         NaN   

      agePossession  \
0  5 to 10 Year Old   
1   0 to 1 Year Old   
2   0 to 1 Year Old   
3   1 to 5 Year Old   
4  5 to 10 Year Old   

                                                                                                                                                                                                                                                                                                                                                        nearbyLocations  \
0                                                                              ['Reach 3 Roads Shopping Mall', 'Southern Periphery Road', 'Indus World School', 'DPG Institute of Technology', 'Polaris Hospital', 'Indira Gandhi International Airport', 'IMT Manesar', 'Radisson Hotel Sohna Road', 'SkyJumper Trampoline Park', 'SportsCube Center(Sports Complex)']   
1                                                                                                                                                                                                                                                                                                                                                                   NaN   
2                                                                                                                                                                                              ['Vatika City Centre Mall', 'NH 48, Sector 78, Gurugram', 'Narayana e Techno School Sec77, Gurgaon', 'SGT UNIVERSITY', 'Genesis Hospital', 'Indira Gandhi Intl Airport']   
3                                                                                         ['Airia Mall', 'Golf Course Extension Road', 'Alpine Convent School', 'DPG Institute of Technology', 'MKD Hospital', 'Indira Gandhi International Airport', 'Lemon Tree Hotel, Sohna Road', 'SkyJumper Trampoline Park', 'DLF Golf and Country Club', 'PVR Drive in Theatre']   
4  ['Amba Clinic', 'Ragave Clinic', 'Sercare Clinic', 'Om Clinic', 'Ram Clinic', 'Kushi Clinic', 'Promla Clinic', 'Shree Balaji Clinic', 'Rathore Imt Hospital', 'Dental Hospital', 'Nidan Hospital and Trauma Centre', 'Sagar Clinic', 'Dr. J. S. Sarkar Clinic', 'Bangali Clinic', 'Yadav Clinic', 'Prakash Hospital

### 2. additionalRoom

- after checking value count i can say there are 5 category of additional room
1. servant room
2. study room
3. pooja room
4. store room
5. others

i can do something like one hot encoding, so if there are no rooms available i can say 0 0 0 0 0

In [109]:
df['additionalRoom'].value_counts()

additionalRoom
not available                                    1597
servant room                                      706
study room                                        250
others                                            225
pooja room                                        165
store room                                         99
study room,servant room                            99
pooja room,servant room                            82
pooja room,study room,servant room,store room      72
servant room,others                                60
pooja room,study room,servant room                 56
pooja room,study room,servant room,others          54
servant room,pooja room                            38
servant room,store room                            33
study room,others                                  29
pooja room,study room                              22
pooja room,others                                  17
pooja room,store room                              15
servant room,study room                            12
pooja room,store room,study room,servant room      12
pooja room,servant room,others                     11
study room,servant room,store room                 11
study room,pooja room                              10
servant room,study room,pooja room,store room      10
study room,servant room,pooja room,store room       8
store room,servant room                             8
study room,servant room,others                      7
study room,pooja room,servant room                  7
pooja room,servant room,store room                  7
pooja room,study room,store room                    7
others,servant room                                 6
servant room,pooja room,store room                  6
store room,pooja room                               5
study room,servant room,store room,pooja room       5
pooja room,servant room,study room,store room       5
pooja room,study room,others                        5
study room,pooja room,store room                    4
study room,servant room,pooja room                  4
servant room,store room,pooja room                  4
study room,pooja room,servant room,store room       3
servant room,study room,pooja room                  3
servant room,others,pooja room                      3
pooja room,study room,store room,servant room       3
servant room,pooja room,study room,store room       3
servant room,study room,store room                  2
study room,store room                               2
store room,pooja room,servant room                  2
store room,pooja room,study room                    2
study room,pooja room,store room,servant room       2
store room,pooja room,study room,servant room       2
servant room,others,store room,pooja room           2
pooja room,store room,servant room                  1
servant room,study room,store room,pooja room       1
store room,study room,servant room                  1
store room,pooja room,servant room,study room       1
store room,study room                               1
study room,others,servant room                      1
others,study room                                   1
servant room,pooja room,store room,study room       1
servant room,study room,others                      1
store room,servant room,pooja room                  1
servant room,store room,study room,pooja room       1
study room,store room,pooja room                    1
servant room,pooja room,study room                  1
store room,servant room,study room,pooja room       1
Name: count, dtype: int64

In [112]:
new_cols = ['study room','servant room','store room', 'pooja room','others']

for col in new_cols:
  df[col] = df['additionalRoom'].str.contains(col,na = False).astype(int)

In [114]:
df.sample(5)[['additionalRoom','study room', 'servant room', 'store room', 'pooja room', 'others']]

additionalRoom  study room  servant room  \
2486  servant room,pooja room,study room           1             1   
3241                       not available           0             0   
2617                       not available           0             0   
1920  pooja room,study room,servant room           1             1   
2892                 servant room,others           0             1   

      store room  pooja room  others  
2486           0           1       0  
3241           0           0       0  
2617           0           0       0  
1920           0           1       0  
2892           0           0       1

In [115]:
df.head()

property_type                     society      sector  price  \
0          flat               tulip ivory3.   sector 70   2.00   
1          flat      capital residences 360  sector 70a   1.69   
2          flat          emaar palm premier   sector 77   2.10   
3          flat                m3m merlin3.   sector 67   2.65   
4          flat  dnha group housing society     manesar   0.75   

   price_per_sqft    area  \
0          8333.0  2400.0   
1          8552.0  1976.0   
2         10500.0  2000.0   
3         12945.0  2047.0   
4          4518.0  1660.0   

                                                                                                             areaWithType  \
0                                           Super Built up area 2400(222.97 sq.m.)Carpet area: 1850 sq.ft. (171.87 sq.m.)   
1  Super Built up area 1976(183.58 sq.m.)Built Up area: 1900 sq.ft. (176.52 sq.m.)Carpet area: 1650 sq.ft. (153.29 sq.m.)   
2  Super Built up area 2000(185.81 sq.m.)Built Up area: 1600 sq.ft. (148.64 sq.m.)Carpet area: 1500 sq.ft. (139.35 sq.m.)   
3  Super Built up area 2047(190.17 sq.m.)Built Up area: 1900 sq.ft. (176.52 sq.m.)Carpet area: 1700 sq.ft. (157.94 sq.m.)   
4                                                                                  Super Built up area 1660(154.22 sq.m.)   

   bedRoom  bathroom balcony additionalRoom  floorNum      facing  \
0      4.0       5.0      3+   servant room       6.0        East   
1      3.0       3.0      3+   servant room       8.0  North-East   
2      3.0       4.0      3+   servant room      11.0         NaN   
3      3.0       3.0       3         others       0.0  North-East   
4      3.0       2.0       2  not available       5.0         NaN   

      agePossession  \
0  5 to 10 Year Old   
1   0 to 1 Year Old   
2   0 to 1 Year Old   
3   1 to 5 Year Old   
4  5 to 10 Year Old   

                                                                                                                                                                                                                                                                                                                                                        nearbyLocations  \
0                                                                              ['Reach 3 Roads Shopping Mall', 'Southern Periphery Road', 'Indus World School', 'DPG Institute of Technology', 'Polaris Hospital', 'Indira Gandhi International Airport', 'IMT Manesar', 'Radisson Hotel Sohna Road', 'SkyJumper Trampoline Park', 'SportsCube Center(Sports Complex)']   
1                                                                                                                                                                                                                                                                                                                                                                   NaN   
2                                                                                                                                                                                              ['Vatika City Centre Mall', 'NH 48, Sector 78, Gurugram', 'Narayana e Techno School Sec77, Gurgaon', 'SGT UNIVERSITY', 'Genesis Hospital', 'Indira Gandhi Intl Airport']   
3                                                                                         ['Airia Mall', 'Golf Course Extension Road', 'Alpine Convent School', 'DPG Institute of Technology', 'MKD Hospital', 'Indira Gandhi International Airport', 'Lemon Tree Hotel, Sohna Road', 'SkyJumper Trampoline Park', 'DLF Golf and Country Club', 'PVR Drive in Theatre']   
4  ['Amba Clinic', 'Ragave Clinic', 'Sercare Clinic', 'Om Clinic', 'Ram Clinic', 'Kushi Clinic', 'Promla Clinic', 'Shree Balaji Clinic', 'Rathore Imt Hospital', 'Dental Hospital', 'Nidan Hospital and Trauma Centre', 'Sagar Clinic', 'Dr. J. S. Sarkar Clinic', 'Bangali Clinic', 'Yadav Clinic', 'Prakash Hospital

## 3. agePossession

In [116]:
df['agePossession'].value_counts()

agePossession
1 to 5 Year Old       1677
5 to 10 Year Old       576
0 to 1 Year Old        531
undefined              338
10+ Year Old           310
Under Construction      93
Within 6 months         70
Within 3 months         26
Dec 2023                22
By 2023                 19
By 2024                 17
Dec 2024                16
Mar 2024                14
Oct 2024                 8
Jan 2024                 8
Aug 2023                 7
Jun 2024                 7
Dec 2025                 7
Nov 2023                 5
Aug 2024                 5
Jul 2024                 4
By 2025                  4
Sep 2023                 4
Oct 2023                 4
Nov 2024                 3
Feb 2024                 3
Jan 2025                 3
May 2024                 3
Oct 2025                 2
Jul 2025                 2
By 2027                  2
Apr 2026                 2
Aug 2025                 2
Jul 2027                 2
Jan 2026                 2
Mar 2025                 2
Sep 2025                 2
Dec 2026                 2
Jun 2027                 2
Sep 2027                 1
Jun 2025                 1
Jan 2028                 1
Jul 2026                 1
Apr 2024                 1
Aug 2026                 1
Mar 2026                 1
Jan 2027                 1
Nov 2025                 1
Name: count, dtype: int64

In [117]:
def categorize_age_possession(value):
    if pd.isna(value):
        return "Undefined"
    if "0 to 1 Year Old" in value or "Within 6 months" in value or "Within 3 months" in value:
        return "New Property"
    if "1 to 5 Year Old" in value:
        return "Relatively New"
    if "5 to 10 Year Old" in value:
        return "Moderately Old"
    if "10+ Year Old" in value:
        return "Old Property"
    if "Under Construction" in value or "By" in value:
        return "Under Construction"
    try:
        # For entries like 'May 2024'
        int(value.split(" ")[-1])
        return "Under Construction"
    except:
        return "Undefined"

In [118]:
df['agePossession'] = df['agePossession'].apply(categorize_age_possession)

In [119]:
df['agePossession'].value_counts()

agePossession
Relatively New        1677
New Property           627
Moderately Old         576
Undefined              340
Old Property           310
Under Construction     287
Name: count, dtype: int64

### furnishDetial -

In [129]:
df.sample(5)[['furnishDetails','features']]

furnishDetails  \
3571                                                                                                                                                                                                                                                                   []   
3727  ['1 Fan', '1 Light', 'No AC', 'No Bed', 'No Chimney', 'No Curtains', 'No Dining Table', 'No Exhaust Fan', 'No Geyser', 'No Modular Kitchen', 'No Microwave', 'No Fridge', 'No Sofa', 'No Stove', 'No TV', 'No Wardrobe', 'No Washing Machine', 'No Water Purifier']   
1335                                                                                                                                                                                                                                                                  NaN   
1573     ['1 Exhaust Fan', '1 Stove', '5 AC', '1 Modular Kitchen', '1 Chimney', 'No Bed', 'No Curtains', 'No Dining Table', 'No Fan', 'No Geyser', 'No Light', 'No Microwave', 'No Fridge', 'No Sofa', 'No TV', 'No Wardrobe', 'No Washing Machine', 'No Water Purifier']   
2386                                                                                                                                                                                                                                                                   []   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                               features  
3571                                                                                                                                                                                                                                                                                                                                                                                                                                  ['Intercom Facility', 'Lift(s)', 'Maintenance Staff', 'Water Storage', 'Park', 'Visitor Parking']  
3727                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                NaN  
1335                                                                                                                                                                                                                                                                                                  ['Feng Shui / Vaastu Compliant', 'Lift(s)', 'Maintenance Staff', 'Swimming Pool', 'Park', 'Piped-gas', 'Security Personnel', 'Shopping Centre', 'Fitness Centre / GYM', 'Club house / Community Center', 'Rain Water Harvesting']  
1573  ['Security / Fire Alarm', 'Feng Shui / Vaastu Compliant', 'Private Garden / Terrace', 'Intercom Facility', 'Lift(s)', 'Centrally Air Conditioned', 'Maintenance Staff', 'Water Storage', 'No open drainage around', 'Bank Attached Property', 'Visitor Parking', 'Swimming Pool', 'Park', 'Security Personnel', 'Natural Light', 'Internet/wi-fi connectivity', 'Airy Rooms', 'Low Density Society', 'Fitness Centre / GYM', 'Waste Disposal', 'Rain Water Harvesting', 'Club house / Community Center', 'Water softening plant']  
2386                      

In [130]:
# Extract all unique furnishings from the furnishDetails column
all_furnishings = []
for detail in df['furnishDetails'].dropna():
    furnishings = detail.replace('[', '').replace(']', '').replace("'", "").split(', ')
    all_furnishings.extend(furnishings)
unique_furnishings = list(set(all_furnishings))

# Define a function to extract the count of a furnishing from the furnishDetails
def get_furnishing_count(details, furnishing):
    if isinstance(details, str):
        if f"No {furnishing}" in details:
            return 0
        pattern = re.compile(f"(\d+) {furnishing}")
        match = pattern.search(details)
        if match:
            return int(match.group(1))
        elif furnishing in details:
            return 1
    return 0

# Simplify the furnishings list by removing "No" prefix and numbers
columns_to_include = [re.sub(r'No |\d+', '', furnishing).strip() for furnishing in unique_furnishings]
columns_to_include = list(set(columns_to_include))  # Get unique furnishings
columns_to_include = [furnishing for furnishing in columns_to_include if furnishing]  # Remove empty strings

# Create new columns for each unique furnishing and populate with counts
for furnishing in columns_to_include:
    df[furnishing] = df['furnishDetails'].apply(lambda x: get_furnishing_count(x, furnishing))

# Create the new dataframe with the required columns
furnishings_df = df[['furnishDetails'] + columns_to_include]

In [131]:
furnishings_df.drop(columns=['furnishDetails'],inplace=True)

<ipython-input-131-e4dadedf8e21>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  furnishings_df.drop(columns=['furnishDetails'],inplace=True)


In [132]:
import matplotlib.pyplot as plt
from sklearn.cluster import KMeans
from sklearn.preprocessing import StandardScaler

In [133]:
scaler = StandardScaler()
scaled_data = scaler.fit_transform(furnishings_df)

In [134]:
wcss_reduced = []

for i in range(1, 11):
    kmeans = KMeans(n_clusters=i, init='k-means++', random_state=42)
    kmeans.fit(scaled_data)
    wcss_reduced.append(kmeans.inertia_)

In [135]:
n_clusters = 3

# Fit the KMeans model
kmeans = KMeans(n_clusters=n_clusters, random_state=42)
kmeans.fit(scaled_data)

# Predict the cluster assignments for each row
cluster_assignments = kmeans.predict(scaled_data)

In [136]:
df = df.iloc[:,:-18]

In [137]:
df['furnishing_type'] = cluster_assignments

In [138]:
df.sample(5)[['furnishDetails','furnishing_type']]
# 0 -> unfurnished
# 1 -> semifurnished
# 2 -> furnished

furnishDetails  \
3083                                                                                                                                                                                                                                                                 NaN   
3442       ['1 Water Purifier', '25 Fan', '1 Fridge', '1 Exhaust Fan', '1 Dining Table', '16 Geyser', '1 Stove', '78 Light', '9 AC', '3 Chimney', '16 Curtains', '1 Modular Kitchen', '28 Wardrobe', 'No Bed', 'No Microwave', 'No Sofa', 'No TV', 'No Washing Machine']   
3801   ['1 Fan', '1 Light', '3 AC', '1 Modular Kitchen', 'No Bed', 'No Chimney', 'No Curtains', 'No Dining Table', 'No Exhaust Fan', 'No Geyser', 'No Microwave', 'No Fridge', 'No Sofa', 'No Stove', 'No TV', 'No Wardrobe', 'No Washing Machine', 'No Water Purifier']   
2900      ['12 Fan', '1 Exhaust Fan', '6 Geyser', '1 Stove', '32 Light', '8 AC', '1 Modular Kitchen', '1 Chimney', '10 Curtains', '10 Wardrobe', '1 Microwave', 'No Bed', 'No Dining Table', 'No Fridge', 'No Sofa', 'No TV', 'No Washing Machine', 'No Water Purifier']   
3461  ['2 Wardrobe', '2 Fan', '2 Light', 'No AC', 'No Bed', 'No Chimney', 'No Curtains', 'No Dining Table', 'No Exhaust Fan', 'No Geyser', 'No Modular Kitchen', 'No Microwave', 'No Fridge', 'No Sofa', 'No Stove', 'No TV', 'No Washing Machine', 'No Water Purifier']   

      furnishing_type  
3083                0  
3442                2  
3801                0  
2900                1  
3461                0

### 5. features

In [139]:
df[['society','features']].sample(5)

society  \
3655      emaar mgf marbella   
2203     mahindra luminare4.   
40              ireo skyon4.   
101            vatika city4.   
64    sidhartha ncr greens4.   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                     features  
3655  ['Centrally Air Conditioned', 'Water purifier', 'Security / Fire Alarm', 'Feng Shui / Vaastu Compliant', 'Private Garden / Terrace', 'High Ceiling Height', 'Maintenance Staff', 'False Ceiling Lighting', 'Water Storage', 'Separate entry for servant room', 'No open drainage around', 'Bank Attached Property', 'Piped-gas', 'Internet/wi-fi connectivity', 'Recently Renovated', 'Visitor Parking', 'Swimming Pool', 'Park', 'Security Personnel', 'Natural Light', 'Airy Rooms', 'Spacious Interiors', 'Low Density Society', 'Waste Disposal', 'Rain Water Harvesting', 'Fitness Centre / GYM', 'Club house / Community Center']  
2203                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            ['Lift(s)', 'Swimming Pool', 'Park', 'Fitness Centre / GYM', 'Club house / Community Center']  
40                                                                                                                                                                                         ['Security / Fire Alarm', 'Power Back-up', 'Feng Shui / Vaastu Compliant', 'Intercom Facility', 'Lift(s)', 'High Ceiling Height', 'Maintenance Staff', 'False Ceiling Lighting', 'Water Storage', 'No open drainage around', 'Piped-gas', 'Visitor Parking', 'Swimming Pool', 'Park', 'Internet/wi-fi connectivity', 'Shopping Centre', 'Fitness Centre / GYM', 'Rain Water Harvesting', 'Club house / Community Center', 'Water softening plant']  
101                                                                                                                                                                                                                                                                                                                                                                                                                                                                                    ['Power Back-up', 'Intercom Facility', 'Lift(s)', 'Swimming Pool', 'Park', 'Shopping Centre', 'Fitness Centre / GYM', 'Club house / Community Center']  
64                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                           ['Lift(s)', 'Park', 'Piped-gas']

In [140]:
df['features'].isnull().sum()

np.int64(643)

In [144]:
import pandas as pd
app_df = pd.read_csv('appartments.csv')
app_df.head(2)

PropertyName                               PropertySubName  \
0  Smartworld One DXP  2, 3, 4 BHK Apartment in Sector 113, Gurgaon   
1           M3M Crown     3, 4 BHK Apartment in Sector 111, Gurgaon   

                                                                                                                                  NearbyLocations  \
0                                           ['Bajghera Road', 'Palam Vihar Halt', 'DPSG Palam Vihar', 'Park Hospital', 'Gurgaon Railway Station']   
1  ['DPSG Palam Vihar Gurugram', 'The NorthCap University', 'Park Hospital, Palam Vihar', 'Pacific D21 Mall', 'Palam Vihar Halt Railway Station']   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                    LocationAdvantages  \
0         {'Bajghera Road': '800 Meter', 'Palam Vihar Halt': '2.5 KM', 'DPSG Palam Vihar': '3.1 KM', 'Park Hospital': '3.1 KM', 'Gurgaon Railway Station': '4.9 KM', 'The NorthCap University': '5.4 KM', 'Dwarka Expy': '1.2 KM', 'Hyatt Place Gurgaon Udyog Vihar': '7.7 KM', 'Dwarka Sector 21, Metro Station': '7.2 KM', 'Pacific D21 Mall': '7.4 KM', 'Indira Gandhi International Airport': '14.7 KM', 'Hamoni Golf Camp': '6.2 KM', 'Fun N Food Waterpark': '8.8 KM', 'Accenture DDC5': '9 KM'}   
1  {'DPSG Palam Vihar Gurugram': '1.4 Km', 'The NorthCap University': '4.4 Km', 'Park Hospital, Palam Vihar': '1.4 Km', 'Pacific D21 Mall': '8.2 Km', 'Palam Vihar Halt Railway Station': '1.2 Km', 'Dwarka Sector 21 Metro Station': '8.1 Km', 'Dwarka Expressway': '450 m', 'Fun N Food Water Park': '8.1 Km', 'Indira Gandhi International Airport': '14.1 Km', 'Tau DeviLal Sports Complex': '11.2 Km', 'Hamoni Golf Camp': '5 Km', 'Hyatt Place': '6.1 Km', 'Altrade Business Centre': '11.2 Km'}   

                                                                          Link  \
0  https://www.99acres.com/smartworld-one-dxp-sector-113-gurgaon-npxid-r400415   
1           https://www.99acres.com/m3m-crown-sector-111-gurgaon-npxid-r404068   

                                                                                                                                                                                                                                                                                                                                                                                           PriceDetails  \
0  {'2 BHK': {'building_type': 'Apartment', 'area_type': 'Carpet Area', 'area': '1,370 sq.ft.', 'price-range': '₹ 2 - 2.4 Cr'}, '3 BHK': {'building_type': 'Apartment', 'area_type': 'Carpet Area', 'area': '1,850 - 2,050 sq.ft.', 'price-range': '₹ 2.25 - 3.59 Cr'}, '4 BHK': {'building_type': 'Apartment', 'area_type': 'Carpet Area', 'area': '2,600 sq.ft.', 'price-range': '₹ 3.24 - 4.56 Cr'}}   
1                                                                                                       {'3 BHK': {'building_type': 'Apartment', 'area_type': 'Super Built-up Area', 'area': '1,605 - 2,170 sq.ft.', 'price-range': '₹ 2.2 - 3.03 Cr'}, '4 BHK': {'building_type': 'Apartment', 'area_type': 'Super Built-up Area', 'area': '2,248 - 2,670 sq.ft.', 'price-range': '₹ 3.08 - 3.73 Cr'}}   

                                                                                                                                   TopFacilities  
0                     ['Swimming Pool', 'Salon', 'Restaurant', 'Spa', 'Cafeteria', 'Sun Deck', '24x7 Security', 'Club House', 'Gated Community']  
1  ['Bowling Alley', 'Mini Theatre', 'Manicured Garden', 'Swimming Pool', 'Flower Garden', 'Reading Lounge', 'Golf Course', 'Barbecue', 'Sauna']

In [145]:
app_df['PropertyName'] = app_df['PropertyName'].str.lower()
temp_df = df[df['features'].isnull()]
temp_df.shape

(643, 27)

In [146]:
x = temp_df.merge(app_df,left_on='society',right_on='PropertyName',how='left')['TopFacilities']

In [147]:
df.loc[temp_df.index,'features'] = x.values

In [148]:
df['features'].isnull().sum()

np.int64(533)

In [149]:
from sklearn.preprocessing import MultiLabelBinarizer
import ast

In [150]:
# Convert the string representation of lists in the 'features' column to actual lists
df['features_list'] = df['features'].apply(lambda x: ast.literal_eval(x) if pd.notnull(x) and x.startswith('[') else [])

# Use MultiLabelBinarizer to convert the features list into a binary matrix
mlb = MultiLabelBinarizer()
features_binary_matrix = mlb.fit_transform(df['features_list'])

# Convert the binary matrix into a DataFrame
features_binary_df = pd.DataFrame(features_binary_matrix, columns=mlb.classes_)

In [151]:
features_binary_df.sample(5)

24/7 Power Backup  24x7 Security  ATM  Aerobics Centre  Airy Rooms  \
1487                  0              0    0                0           1   
2367                  0              0    0                0           1   
575                   0              0    0                0           0   
1063                  0              0    0                0           0   
3716                  0              0    0                0           0   

      Amphitheatre  Badminton Court  Bank Attached Property  Banquet Hall  \
1487             0                0                       0             0   
2367             0                0                       1             0   
575              0                0                       0             0   
1063             0                0                       0             0   
3716             0                0                       1             0   

      Bar/Chill-Out Lounge  Barbecue  Basketball Court  Billiards  \
1487                     0         0                 0          0   
2367                     0         0                 0          0   
575                      0         0                 0          0   
1063                     0         0                 0          0   
3716                     0         0                 0          0   

      Bowling Alley  Bus Shelter  Business Lounge  CCTV Camera Security  \
1487              0            0                0                     0   
2367              0            0                0                     0   
575               0            0                0                     0   
1063              0            0                0                     0   
3716              0            0                0                     0   

      Cafeteria  Card Room  Centrally Air Conditioned  Changing Area  \
1487          0          0                          0              0   
2367          0          0                          1              0   
575           0          0                          0              0   
1063          0          0                          0              0   
3716          0          0                          0              0   

      Children's Play Area  Cigar Lounge  Clinic  Club House  \
1487                     0             0       0           0   
2367                     0             0       0           0   
575                      0             0       0           0   
1063                     0             0       0           0   
3716                     0             0       0           0   

      Club house / Community Center  Community Hall  Concierge Service  \
1487                              0               0                  0   
2367                              1               0                  0   
575                               0               0                  0   
1063                              0               0                  0   
3716                              1               0                  0   

      Conference room  Creche/Day care  Cricket Pitch  Doctor on Call  \
1487                0                0              0               0   
2367                0                0              0               0   
575                 0                0              0               0   
1063                0                0              0               0   
3716                0                0              0               0   

      Earthquake Resistant  Entrance Lobby  False Ceiling Lighting  \
1487                     0               0                       0   
2367                     0               0                       1   
575                      0               0                       0   
1063                     0               0                       0   
3716                     0               0                       0   

      Feng Shui / Vaastu Compliant  Fire Fighting Systems  \
1487                             0  

In [152]:
features_binary_df.shape

(3817, 121)

In [153]:
wcss_reduced = []

for i in range(1, 11):
    kmeans = KMeans(n_clusters=i, init='k-means++', random_state=42)
    kmeans.fit(features_binary_df)
    wcss_reduced.append(kmeans.inertia_)

In [155]:
# Define the weights for each feature as provided
# Assigning weights based on perceived luxury contribution
weights = {
    '24/7 Power Backup': 8,
    '24/7 Water Supply': 4,
    '24x7 Security': 7,
    'ATM': 4,
    'Aerobics Centre': 6,
    'Airy Rooms': 8,
    'Amphitheatre': 7,
    'Badminton Court': 7,
    'Banquet Hall': 8,
    'Bar/Chill-Out Lounge': 9,
    'Barbecue': 7,
    'Basketball Court': 7,
    'Billiards': 7,
    'Bowling Alley': 8,
    'Business Lounge': 9,
    'CCTV Camera Security': 8,
    'Cafeteria': 6,
    'Car Parking': 6,
    'Card Room': 6,
    'Centrally Air Conditioned': 9,
    'Changing Area': 6,
    "Children's Play Area": 7,
    'Cigar Lounge': 9,
    'Clinic': 5,
    'Club House': 9,
    'Concierge Service': 9,
    'Conference room': 8,
    'Creche/Day care': 7,
    'Cricket Pitch': 7,
    'Doctor on Call': 6,
    'Earthquake Resistant': 5,
    'Entrance Lobby': 7,
    'False Ceiling Lighting': 6,
    'Feng Shui / Vaastu Compliant': 5,
    'Fire Fighting Systems': 8,
    'Fitness Centre / GYM': 8,
    'Flower Garden': 7,
    'Food Court': 6,
    'Foosball': 5,
    'Football': 7,
    'Fountain': 7,
    'Gated Community': 7,
    'Golf Course': 10,
    'Grocery Shop': 6,
    'Gymnasium': 8,
    'High Ceiling Height': 8,
    'High Speed Elevators': 8,
    'Infinity Pool': 9,
    'Intercom Facility': 7,
    'Internal Street Lights': 6,
    'Internet/wi-fi connectivity': 7,
    'Jacuzzi': 9,
    'Jogging Track': 7,
    'Landscape Garden': 8,
    'Laundry': 6,
    'Lawn Tennis Court': 8,
    'Library': 8,
    'Lounge': 8,
    'Low Density Society': 7,
    'Maintenance Staff': 6,
    'Manicured Garden': 7,
    'Medical Centre': 5,
    'Milk Booth': 4,
    'Mini Theatre': 9,
    'Multipurpose Court': 7,
    'Multipurpose Hall': 7,
    'Natural Light': 8,
    'Natural Pond': 7,
    'Park': 8,
    'Party Lawn': 8,
    'Piped Gas': 7,
    'Pool Table': 7,
    'Power Back up Lift': 8,
    'Private Garden / Terrace': 9,
    'Property Staff': 7,
    'RO System': 7,
    'Rain Water Harvesting': 7,
    'Reading Lounge': 8,
    'Restaurant': 8,
    'Salon': 8,
    'Sauna': 9,
    'Security / Fire Alarm': 9,
    'Security Personnel': 9,
    'Separate entry for servant room': 8,
    'Sewage Treatment Plant': 6,
    'Shopping Centre': 7,
    'Skating Rink': 7,
    'Solar Lighting': 6,
    'Solar Water Heating': 7,
    'Spa': 9,
    'Spacious Interiors': 9,
    'Squash Court': 8,
    'Steam Room': 9,
    'Sun Deck': 8,
    'Swimming Pool': 8,
    'Temple': 5,
    'Theatre': 9,
    'Toddler Pool': 7,
    'Valet Parking': 9,
    'Video Door Security': 9,
    'Visitor Parking': 7,
    'Water Softener Plant': 7,
    'Water Storage': 7,
    'Water purifier': 7,
    'Yoga/Meditation Area': 7
}
# Calculate luxury score for each row
# Add missing columns and fill with 0
for feature in weights:
    if feature not in features_binary_df.columns:
        features_binary_df[feature] = 0

# Now it's safe to compute luxury score
luxury_score = features_binary_df[list(weights.keys())].multiply(list(weights.values())).sum(axis=1)

In [156]:
df['luxury_score'] = luxury_score

In [158]:
df[df['society'] == 'signature global park 4']

property_type                  society          sector  price  \
236           flat  signature global park 4  sector 36 road   0.82   
624           flat  signature global park 4  sector 36 road   0.82   
1606          flat  signature global park 4  sector 36 road   0.72   
2162          flat  signature global park 4  sector 36 road   0.72   
2587          flat  signature global park 4  sector 36 road   1.00   
3020          flat  signature global park 4  sector 36 road   0.85   

      price_per_sqft    area  \
236           7585.0  1081.0   
624           7585.0  1081.0   
1606          6660.0  1081.0   
2162          6428.0  1120.0   
2587          9900.0  1010.0   
3020         11333.0   750.0   

                                                                     areaWithType  \
236   Super Built up area 1081(100.43 sq.m.)Carpet area: 650 sq.ft. (60.39 sq.m.)   
624                                              Carpet area: 1081 (100.43 sq.m.)   
1606                                       Super Built up area 1081(100.43 sq.m.)   
2162                                             Carpet area: 1120 (104.05 sq.m.)   
2587                                              Carpet area: 1010 (93.83 sq.m.)   
3020                                               Carpet area: 750 (69.68 sq.m.)   

      bedRoom  bathroom balcony additionalRoom  floorNum facing  \
236       3.0       2.0       2  not available       2.0    NaN   
624       3.0       2.0       3  not available       2.0    NaN   
1606      3.0       2.0       3  not available       3.0    NaN   
2162      3.0       2.0       3  not available       2.0    NaN   
2587      3.0       2.0       3  not available       2.0    NaN   
3020      3.0       2.0       3  not available       1.0    NaN   

           agePossession  \
236         New Property   
624         New Property   
1606  Under Construction   
2162  Under Construction   
2587        New Property   
3020        New Property   

                                                                                                                                                                                                                                                                                                 nearbyLocations  \
236   ['Sector 55-56 Metro Station', 'The Leaf Mall Sohna', 'Omaxe Gurgaon Mall', 'Badshahpur Sohna Rd Hwy', 'Vidya Niketan School', 'KIIT College of Engg', 'Scottish High International School', 'Rawal Institutions', 'Park Hospital', 'Indira Gandhi Intl Airport', 'Spaze Business Park', 'DLF Cyber City']   
624   ['Sector 55-56 Metro Station', 'The Leaf Mall Sohna', 'Omaxe Gurgaon Mall', 'Badshahpur Sohna Rd Hwy', 'Vidya Niketan School', 'KIIT College of Engg', 'Scottish High International School', 'Rawal Institutions', 'Park Hospital', 'Indira Gandhi Intl Airport', 'Spaze Business Park', 'DLF Cyber City']   
1606                                                                                                                                                                                                                                                                                                         NaN   
2162  ['Sector 55-56 Metro Station', 'The Leaf Mall Sohna', 'Omaxe Gurgaon Mall', 'Badshahpur Sohna Rd Hwy', 'Vidya Niketan School', 'KIIT College of Engg', 'Scottish High International School', 'Rawal Institutions', 'Park Hospital', 'Indira Gandhi Intl Airport', 'Spaze Business Park', 'DLF Cyber City']   
2587  ['Sector 55-56 Metro Station', 'The Leaf Mall Sohna', 'Omaxe Gurgaon Mall', 'Badshahpur Sohna Rd Hwy', 'Vidya Niketan School', 'KIIT College of Engg', 'Scottish High International School', 'Rawal Institutions', 'Park Hospital', 'Indira Gandhi Intl Airport', 'Spaze Business Park', 'DLF Cyber City']   
3020  ['Sector 55-56 Metro Station', 'The Leaf Mall Sohna', 'Omaxe Gurgaon Mall', 'Badshahpur Sohna Rd Hwy', 'Vidya Niketan School', 'KIIT College of Engg', 'Scottish High Intern

In [160]:
# cols to drop -> nearbyLocations,furnishDetails, features,features_list, additionalRoom
df.drop(columns=['nearbyLocations','furnishDetails','features','features_list','additionalRoom'],inplace=True)

In [161]:
df.shape

(3817, 24)

In [162]:
df.columns

Index(['property_type', 'society', 'sector', 'price', 'price_per_sqft', 'area',
       'areaWithType', 'bedRoom', 'bathroom', 'balcony', 'floorNum', 'facing',
       'agePossession', 'super_built_up_area', 'built_up_area',
       'build_up_area', 'carpet_area', 'study room', 'servant room',
       'store room', 'pooja room', 'others', 'furnishing_type',
       'luxury_score'],
      dtype='object')

In [163]:
df['build_up_area']

0             NaN
1         1900.00
2         1600.00
3         1900.00
4             NaN
5             NaN
6             NaN
7             NaN
8             NaN
9             NaN
10            NaN
11         480.00
12            NaN
13            NaN
14            NaN
15            NaN
16            NaN
17            NaN
18            NaN
19        2779.00
20        1535.00
21            NaN
22            NaN
23        1870.00
24        1330.00
25        2040.00
26            NaN
27        2000.00
28            NaN
29            NaN
30            NaN
31            NaN
32            NaN
33            NaN
34            NaN
35            NaN
36        1210.00
37            NaN
38            NaN
39            NaN
40            NaN
41        1900.00
42            NaN
43            NaN
44        3225.00
45            NaN
46         915.00
47            NaN
48            NaN
49        1000.00
50            NaN
51            NaN
52            NaN
53        1285.00
54            NaN
55            NaN
56            NaN
57        1485.00
58        1420.00
59            NaN
60            NaN
61            NaN
62            NaN
63         850.00
64            NaN
65            NaN
66        1250.00
67            NaN
68            NaN
69            NaN
70            NaN
71        1700.00
72            NaN
73            NaN
74        1150.00
75            NaN
76            NaN
77            NaN
78        1900.00
79        3850.00
80            NaN
81            NaN
82            NaN
83        1500.00
84            NaN
85        1600.00
86         720.00
87         192.00
88            NaN
89            NaN
90        3831.00
91         425.00
92            NaN
93            NaN
94        1480.00
95            NaN
96        1000.00
97        3655.35
98            NaN
99            NaN
100           NaN
101           NaN
102       2040.00
103           NaN
104           NaN
105       2400.00
106           NaN
107           NaN
108           NaN
109       1081.00
110           NaN
111           NaN
112       2343.00
113           NaN
114           NaN
115           NaN
116           NaN
117           NaN
118           NaN
119           NaN
120           NaN
121       1797.00
122        500.00
123           NaN
124       2000.00
125           NaN
126           NaN
127           NaN
128       1750.00
129           NaN
130       1730.00
131       2000.00
132           NaN
133           NaN
134       1690.00
135           NaN
136           NaN
137       2480.00
138       1720.00
139           NaN
140       1305.00
141           NaN
142           NaN
143           NaN
144           NaN
145           NaN
146       1600.00
147           NaN
148           NaN
149           NaN
150       2600.00
151           NaN
152       2625.00
153           NaN
154           NaN
155           NaN
156           NaN
157           NaN
158       1000.00
159           NaN
160           NaN
161           NaN
162       1365.00
163           NaN
164       1137.00
165       2835.00
166       1300.00
167       1471.12
168           NaN
169       1090.00
170           NaN
171           NaN
172           NaN
173           NaN
174           NaN
175           NaN
176           NaN
177           NaN
178        750.00
179           NaN
180           NaN
181           NaN
182           NaN
183        340.00
184           NaN
185        140.00
186           NaN
187           NaN
188           NaN
189           NaN
190           NaN
191        301.00
192        565.00
193       2000.00
194           NaN
195           NaN
196           NaN
197           NaN
198           NaN
199           NaN
200           NaN
201           NaN
202       1500.00
203        162.00
204           NaN
205       7000.00
206        300.00
207           NaN
208           NaN
209           NaN
210           NaN
211       3900.00
212       1350.00
213           NaN
214           NaN
215           NaN
216           NaN
217           NaN
218           NaN
219       1130.00
220           NaN
221        846.00
222 

In [164]:
df

property_type                                            society  \
0             flat                                      tulip ivory3.   
1             flat                             capital residences 360   
2             flat                                 emaar palm premier   
3             flat                                       m3m merlin3.   
4             flat                         dnha group housing society   
5             flat                                 godrej nature plus   
6            house                                        independent   
7             flat                                    godrej summit3.   
8             flat                            signature global park4.   
9             flat                                  indiabulls enigma   
10            flat                                   smart world gems   
11           house             surendra homes dayaindependentd colony   
12           house                                 ansals palam vihar   
13            flat                      bestech park view residency3.   
14            flat                                         rof ananda   
15            flat                           bestech park view city4.   
16            flat                           vatika the seven lamps3.   
17            flat                     signature global city 37d ph 2   
18            flat                                aipl zen residences   
19            flat                           experion the heartsong3.   
20            flat                     signature global city 37d ph 2   
21            flat                                         rof ananda   
22            flat                                         sare homes   
23            flat                                   unitech fresco3.   
24            flat                                   unitech fresco3.   
25            flat                                  sare green parc 2   
26            flat                                   ats tourmaline3.   
27            flat                                vatika gurgaon 213.   
28           house                international city by sobha phase 2   
29           house                                 emaar mgf marbella   
30           house                                        independent   
31            flat                                      m3m soulitude   
32            flat                             breez global heights4.   
33            flat                           puri diplomatic greens4.   
34            flat                                    orchid petals4.   
35            flat                                      ats triumph3.   
36            flat                            signature global park4.   
37            flat                        adani brahma samsara vilasa   
38            flat                                        m3m skywalk   
39           house                                 ansals palam vihar   
40            flat                                       ireo skyon4.   
41            flat                                    kiran residency   
42           house                                        independent   
43            flat                                 dlf royalton tower   
44            flat                              vatika sovereign park   
45            flat                  signature global orchard avenue3.   
46            flat               shapoorji pallonji joyville gurugram   
47            flat                                         ss almeria   
48           house                                        independent   
49            flat                                 vatika inxt floors   
50           house                                        independent   
51            flat                                          apartment   
52           house                                        independent   
53            flat                                 ambience cre

In [165]:
df.head()

property_type                     society      sector  price  \
0          flat               tulip ivory3.   sector 70   2.00   
1          flat      capital residences 360  sector 70a   1.69   
2          flat          emaar palm premier   sector 77   2.10   
3          flat                m3m merlin3.   sector 67   2.65   
4          flat  dnha group housing society     manesar   0.75   

   price_per_sqft    area  \
0          8333.0  2400.0   
1          8552.0  1976.0   
2         10500.0  2000.0   
3         12945.0  2047.0   
4          4518.0  1660.0   

                                                                                                             areaWithType  \
0                                           Super Built up area 2400(222.97 sq.m.)Carpet area: 1850 sq.ft. (171.87 sq.m.)   
1  Super Built up area 1976(183.58 sq.m.)Built Up area: 1900 sq.ft. (176.52 sq.m.)Carpet area: 1650 sq.ft. (153.29 sq.m.)   
2  Super Built up area 2000(185.81 sq.m.)Built Up area: 1600 sq.ft. (148.64 sq.m.)Carpet area: 1500 sq.ft. (139.35 sq.m.)   
3  Super Built up area 2047(190.17 sq.m.)Built Up area: 1900 sq.ft. (176.52 sq.m.)Carpet area: 1700 sq.ft. (157.94 sq.m.)   
4                                                                                  Super Built up area 1660(154.22 sq.m.)   

   bedRoom  bathroom balcony  floorNum      facing   agePossession  \
0      4.0       5.0      3+       6.0        East  Moderately Old   
1      3.0       3.0      3+       8.0  North-East    New Property   
2      3.0       4.0      3+      11.0         NaN    New Property   
3      3.0       3.0       3       0.0  North-East  Relatively New   
4      3.0       2.0       2       5.0         NaN  Moderately Old   

   super_built_up_area  built_up_area  build_up_area  carpet_area  study room  \
0               2400.0            NaN            NaN       1850.0           0   
1               1976.0         1900.0         1900.0       1650.0           0   
2               2000.0         1600.0         1600.0       1500.0           0   
3               2047.0         1900.0         1900.0       1700.0           0   
4               1660.0            NaN            NaN          NaN           0   

   servant room  store room  pooja room  others  furnishing_type  luxury_score  
0             1           0           0       0                1            95  
1             1           0           0       0                0           165  
2             1           0           0       0                1           129  
3             0           0           0       1                1           174  
4             0           0           0       0                0             0

In [166]:
duplicates = features_binary_df.columns[features_binary_df.columns.duplicated()]
print("Duplicate columns:", duplicates.tolist())

Duplicate columns: []


In [167]:
features_binary_df = features_binary_df.loc[:, ~features_binary_df.columns.duplicated()]

In [168]:
df.columns

Index(['property_type', 'society', 'sector', 'price', 'price_per_sqft', 'area',
       'areaWithType', 'bedRoom', 'bathroom', 'balcony', 'floorNum', 'facing',
       'agePossession', 'super_built_up_area', 'built_up_area',
       'build_up_area', 'carpet_area', 'study room', 'servant room',
       'store room', 'pooja room', 'others', 'furnishing_type',
       'luxury_score'],
      dtype='object')

In [171]:
(df['built_up_area'] == df['build_up_area']).all()

np.False_

In [172]:
df.drop(columns='build_up_area', inplace=True)

In [173]:
df.shape

(3817, 23)

In [174]:
df.to_csv('gurgaon_properties_cleaned_v2.csv',index=False)